In [1]:
from glob import glob
from os.path import join
import pandas as pd
import numpy as np

from maps.pings import Pings
from maps.maps import FoliumMap

location_data_dirpath = '../../data/locations/'
photo_metadata_dirpath = '../../data/photo_metadata'

pings_data_path = join(location_data_dirpath, 'pings.hdf')
posts_path = join(photo_metadata_dirpath, 'posts.hdf')

%reload_ext autoreload
%autoreload 2

In [2]:
# load geolocated photos
posts = pd.read_hdf(posts_path, 'data')
photos = posts[~posts.latitude.isna()]

In [3]:
# import pickle

# # load all pings
# ping_data = pd.read_hdf(pings_data_path, 'data')
# ping_data = ping_data[ping_data.accuracy < 3000]
# ping_data = ping_data[ping_data.altitude < 4000]

# # geocode trip pings
# pings = Pings(ping_data.loc['2019-07-24':], 2)
# pings.cluster(use_weights=False, n_clusters=500)
# pings.build_geocodes()
# pings.geocode()

# #save clustered pings
# pickled_pings_path = join(location_data_dirpath, 'clustered_pings.pkl')
# with open(pickled_pings_path, 'wb') as file:
#     pickle.dump(pings, file)

In [1071]:
# from scipy.spatial import distance, distance_matrix
# from modules.utilities import haversine
# import numpy as np

# def compute_max_distance(df):
#     xy = df[trip.GPS_INDEX].values
#     if xy.shape[0] <= 1:
#         return np.nan
#     else:
#         max_distance = distance.pdist(xy, metric=haversine).max()
#         return max_distance
    
# def compute_mean_speed(df):
#     if len(df) <= 1:
#         return np.nan
#     total_hours = (df.index.max() - df.index.min()).total_seconds() / 3600
#     xy = df[trip.GPS_INDEX].values
#     total_miles = sum([haversine(a,b) for a, b in zip(xy[:-1], xy[1:])])
#     mean_speed = total_miles / total_hours
#     return mean_speed

# window_size = 60

# pings._pings['window_max_distance'] = None
# pings._pings['window_velocity'] = None

# for owner, df in pings._pings.groupby('owner'):
#     time_window = df.loc[owner].index.round("{:d}T".format(window_size))
#     speed_per_time_window = df.loc[owner].groupby(time_window).apply(compute_mean_speed)
#     max_distance_per_time_window = df.loc[owner].groupby(time_window).apply(compute_max_distance)
#     pings._pings.loc[owner, 'window_velocity'] = speed_per_time_window.loc[time_window].values
#     pings._pings.loc[owner, 'window_max_distance'] = max_distance_per_time_window.loc[time_window].values
    
# #save clustered pings
# pickled_pings_path = join(location_data_dirpath, 'clustered_pings.pkl')
# with open(pickled_pings_path, 'wb') as file:
#     pickle.dump(pings, file)

In [3]:
import pickle

# load clustered pings
pickled_pings_path = join(location_data_dirpath, 'clustered_pings.pkl')
with open(pickled_pings_path, 'rb') as file:
    pings = pickle.load(file)

In [137]:
trip_ids = {'Highway 1': ('2019-07-24 00:10:30', '2019-08-02 10:00:00'),
 'France': ('2019-08-12 03:50:39', '2019-08-20 21:04:50'),
 'Italian Coast': ('2019-08-20 16:35:51', '2019-09-11 10:20:21'),
 'England': ('2019-09-11 08:18:40', '2019-09-25 14:31:47'),
 'Central Europe': ('2019-09-25 12:19:46', '2019-10-22 12:09:37'),
 'Catalonia': ('2019-11-02 11:49:07', '2019-11-07 14:22:22'),
 'Morocco': ('2019-12-03 20:36:19', '2019-12-13 02:15:52'),
 'Italian Alps': ('2019-12-13 10:43:52', '2019-12-24 03:23:37'),
 'Bay Area': ('2020-01-01 00:00:00', '2020-02-24 00:00:00'),
 'Rocky Mountains': ('2020-02-25 00:07:38', '2020-03-18 23:57:50')}

pings.label_timespans('trip_id', trip_ids)

In [138]:
# drives, flights = trips.segments['land'], trips.segments['air']

# highway1_drive = [d for d in drives if 'San Diego' in d.cities][0]
# france_flights = [f for f in flights if 'FR' in f.countries and f.stop_ts<'2019-11-01']
# italian_coast_flights = [f for f in flights if 'IT' in f.countries and f.stop_ts<'2019-11-01']
# england_flights = [f for f in flights if 'GB' in f.countries and f.stop_ts < '2019-09-26']
# central_europe_flights = [f for f in flights if 'CZ' in f.countries]
# catalonia_flights = [f for f in flights if 'ES' in f.countries and f.stop_ts<'2019-12-01']
# morocco_flights = [f for f in flights if 'MA' in f.countries]
# italian_alps_flights = [f for f in flights if 'IT' in f.countries and f.start_ts>'2019-12-01']
# rockies_drive = [d for d in drives if 'Wyoming' in d.states][0]

# # label trips
# trip_ids = {
#     'Highway 1': (highway1_drive.start_ts, highway1_drive.stop_ts),
#     'France': (france_flights[0].start_ts, france_flights[-1].stop_ts),
#     'Italian Coast': (italian_coast_flights[0].start_ts, italian_coast_flights[-1].stop_ts),
#     'England': (england_flights[0].start_ts, england_flights[-1].stop_ts),
#     'Central Europe': (central_europe_flights[0].start_ts, central_europe_flights[-1].stop_ts),
#     'Catalonia': (catalonia_flights[0].start_ts, catalonia_flights[-1].stop_ts),
#     'Morocco': (morocco_flights[0].start_ts, morocco_flights[-1].stop_ts),
#     'Italian Alps': (italian_alps_flights[0].start_ts, italian_alps_flights[-1].stop_ts),
#     'Rocky Mountains': (rockies_drive.start_ts, rockies_drive.stop_ts)
# }

# Composite map

In [139]:
from maps.trips import TripGenerator

In [144]:
# compile trip generator
trips = TripGenerator(pings, photos)

# mark returns
for flight in trips.segments['air']:
    if 'California' in flight.destination.state:
        flight.add_trip_id('Return Flights')
    if 'Berlin' in flight.origin_str:
        flight.add_trip_id('Return Flights')

/Users/Sebi/Documents/websites/sbernasek/code/maps/trips.py:258: RuntimeWarning: divide by zero encountered in true_divide
  for idx in np.logical_and(dx > 250, (dx/dt)>50).nonzero()[0]:


# Generate trip

In [ ]:
"""
- smooth drives
- add hikes/ski days

- fix photo captions
- photo centering/lightbox
"""

In [157]:
# world
trip_ids = ['Highway 1', 'France', 'Italian Coast', 'England', 'Central Europe', 'Catalonia', 'Morocco', 'Italian Alps', 'Bay Area', 'Rocky Mountains', 'Return Flights']
location = [  45.663463, -49.071684  ]
zoom_start = 2
filename = 'merge.html'
timespans = None

# # roadtrips
# trip_ids = ['Highway 1']
# location = None
# zoom_start = 6
# filename = '2019_summer.html'
# timespans = [('2019:07:15 00:00:00', '2019:08:11 00:00:00'),]
# timespans = [[str_to_datetime(t) for t in ts] for ts in timespans]


# # europe 1
# trip_ids = ['France', 'Italian Coast', 'England', 'Central Europe', 'Catalonia', 'Return Flights']
# location = [  45.438766, 7.669425  ]
# zoom_start = 5
# filename = '2019_fall.html'
# timespans = [('2019:08:11 00:00:00', '2019:11:15 00:00:00'),]
# timespans = [[str_to_datetime(t) for t in ts] for ts in timespans]


# # morocco/italy
# trip_ids = ['Morocco', 'Italian Alps', 'Return Flights']
# location = [  39.371827, 1.987188  ]
# zoom_start = 5
# filename = '2019_winter.html'
# timespans = [('2019:12:01 00:00:00', '2019:12:25 00:00:00'),]
# timespans = [[str_to_datetime(t) for t in ts] for ts in timespans]


# # roadtrips
# trip_ids = ['Bay Area', 'Rocky Mountains']
# location = [  38.945276, -116.531555  ]
# zoom_start = 5
# filename = '2020_spring.html'
# timespans = [('2020:01:01 00:00:00', '2020:03:20 00:00:00'),]
# timespans = [[str_to_datetime(t) for t in ts] for ts in timespans]


trip = trips.get_trip(*trip_ids, timespans=timespans)
trip.build_map(location=location, zoom_start=zoom_start, max_zoom=16)
trip.add_photos_to_map(True, maxClusterRadius=50, disableClusteringAtZoom=10, zoomToBoundsOnClick=True)
trip.add_heatmap_to_map(show=True, radius=20, blur=30, max_zoom=12, min_opacity=0., max_val=3.)
trip.add_travel_to_map(weight=3, drive_color='black', show=False,
                       drive_kwargs={'min_velocity': None, 'min_distance': None, 'freq': None})
trip.add_layer_control()

In [158]:
trip.map

In [159]:
trip.save_map('../travel/maps/{:s}'.format(filename))

In [ ]:
"""
Full Map
Europe 1
Morocco/Italy
Roadtrips
"""

In [ ]:
IFrame()

In [563]:
m = FoliumMap()
m.build_map(xy.values.mean(axis=0))
m.add_bubbles(xy.values, radius=5)
m.map

In [237]:
xy = drive.data[drive.GPS_INDEX]

In [256]:
drive.data['path_length'] = pd.concat([xy, xy.shift(1)], axis=1).apply(lambda x: haversine(x.iloc[:2], x.iloc[2:]), axis=1)
drive.data['path_progress'] = drive.data.distance.cumsum()
distance_from_origin = drive.data[drive.GPS_INDEX].apply(lambda x: haversine(x, drive.data[drive.GPS_INDEX].iloc[0]), axis=1)
drive.data['distance_from_origin'] = distance_from_origin

In [804]:
XY = drive.data[drive.GPS_INDEX].values

In [805]:
from sklearn.cluster import MeanShift

In [806]:
ms=MeanShift(bandwidth=1)

In [807]:
ms.fit(XY)

MeanShift(bandwidth=1, bin_seeding=False, cluster_all=True, max_iter=300,
          min_bin_freq=1, n_jobs=None, seeds=None)

In [830]:
# import requests

# responses = {}
# for segment in trips.segments['air'] + trips.segments['rail']:
#     for port in (segment.origin, segment.destination):
#         gps = tuple(port[segment.GPS_INDEX].values.tolist())
#         query = 'https://api.aerisapi.com/places/closest?p={:2.6f},{:2.6f}&query=pop:250000&radius=50mi&limit=5&client_id={:s}&client_secret={:s}'.format(*gps, aeris_keys['ACCESS_ID'],aeris_keys['SECRET_KEY'])
#         response = requests.get(query)
#         responses[gps] = sorted(response.json()['response'], key=lambda x: x['relativeTo']['distanceKM'], reverse=False)